In [1]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.feature_selection import SelectKBest, f_classif



In [2]:
features_df = pd.read_csv("PI-CAI_features")
labels_df = pd.read_csv("marksheet.csv")



In [3]:
labels_df.rename(columns={'patient_id': 'patient_ID', 'study_id': 'study_ID'}, inplace=True)
labels_df['case_csPCa'] = labels_df['case_csPCa'].map(lambda x: 1 if x == 'YES' else 0)


In [4]:
df_ai = features_df[
    (features_df['annotator'] == 'AI') &
    (features_df['ROI'] == 'lesion') &
    (features_df['sequence'].isin(['adc', 't2w', 'hbv']))
].copy()

exclude_cols = ['annotator', 'ROI', 'ROI_ID', 'img_path', 'seg_path', 'extraction_ID']
df_ai_clean = df_ai.drop(columns=exclude_cols).copy()
df_ai_clean['sequence'] = df_ai_clean['sequence'].astype(str)
df_ai_clean.set_index(['patient_ID', 'study_ID', 'sequence'], inplace=True)


In [5]:
df_wide = df_ai_clean.unstack(level=-1)
df_wide.columns = [f"{seq}_{col}" for col, seq in df_wide.columns]
df_wide.reset_index(inplace=True)

In [16]:
print(df_ai_clean.columns.size, df_wide.columns.size)

1015 3047


In [6]:
df_final = df_wide.merge(labels_df, on=['patient_ID', 'study_ID'], how='inner')
y = df_final['case_csPCa']
X = df_final.drop(columns=['patient_ID', 'study_ID', 'case_csPCa'])


In [20]:
X

adc_original_shape_Elongation  hbv_original_shape_Elongation  \
0                         0.733925                       0.733925   
1                         0.223764                       0.223764   
2                         0.569978                       0.569978   
3                         0.914667                       0.914667   
4                         0.714127                       0.714127   
..                             ...                            ...   
403                       0.831726                       0.831726   
404                       0.563701                       0.563701   
405                       0.941727                       0.941727   
406                       0.413306                       0.413306   
407                       0.730637                       0.730637   

     t2w_original_shape_Elongation  adc_original_shape_Flatness  \
0                         0.810849                     0.556818   
1                         0.219432                     0.174031   
2                         0.561657                     0.353260   
3                         0.947138                     0.804680   
4                         1.000000                     0.659643   
..                             ...                          ...   
403                       0.831726                     0.622951   
404                       0.517514                     0.542741   
405                       0.861388                     0.791911   
406                       0.392137                     0.294534   
407                       0.688051                     0.511871   

     hbv_original_shape_Flatness  t2w_original_shape_Flatness  \
0                       0.556818                     0.536311   
1                       0.174031                     0.187087   
2                       0.353260                     0.342182   
3                       0.804680                     0.858744   
4                       0.659643                     0.750000   
..                           ...                          ...   
403                     0.622951                     0.622951   
404                     0.542741                     0.473542   
405                     0.791911                     0.818372   
406                     0.294534                     0.303200   
407                     0.511871                     0.442278   

     adc_original_shape_LeastAxisLength  hbv_original_shape_LeastAxisLength  \
0                              6.292914                            6.292914   
1                              9.527915                            9.527915   
2                              7.127349                            7.127349   
3                              8.315141                            8.315141   
4                              5.020273                            5.020273   
..                                  ...                                 ...   
403                           10.157247                           10.157247   
404                            7.190927                            7.190927   
405                            9.809743                            9.809743   
406                            6.688317                            6.688317   
407                            6.531868                            6.531868   

     t2w_original_shape_LeastAxisLength  adc_original_shape_MajorAxisLength  \
0                              5.872887                           11.301554   
1                             10.296406                           54.748291   
2                              6.991918                           20.175907   
3                              8.432565                           10.333475   
4                              5.196152                            7.610592   
..                                  ...                                 ...   
403                           10.157247                           16.305044   
404      

In [7]:
sequence_combinations = {
    "ADC": ['adc'],
    "T2W": ['t2w'],
    "HBV": ['hbv'],
    "ADC + T2W": ['adc', 't2w'],
    "ADC + HBV": ['adc', 'hbv'],
    "T2W + HBV": ['t2w', 'hbv'],
    "ADC + T2W + HBV": ['adc', 't2w', 'hbv']
}

In [8]:
pca_selected_features = {}
anova_selected_features = {}

In [9]:
for name, prefixes in sequence_combinations.items():
    cols = [col for col in X.columns if any(col.startswith(prefix) for prefix in prefixes)]
    if not cols:
        continue
    X_subset = X[cols].fillna(X[cols].median())
    scaler = StandardScaler()
    X_scaled = scaler.fit_transform(X_subset)
    pca = PCA(n_components=0.90)
    pca.fit(X_scaled)
    loadings = abs(pca.components_).sum(axis=0)
    feature_scores = dict(zip(X_subset.columns, loadings))
    sorted_features = sorted(feature_scores.items(), key=lambda x: -x[1])
    pca_selected_features[name] = [f for f, _ in sorted_features]


# PCA: selezione unsupervised

In [10]:

pca = PCA(n_components=0.90)
X_pca = pca.fit_transform(X_scaled)
loadings = np.abs(pca.components_).sum(axis=0)
top_indices = np.argsort(loadings)[::-1][:50]
pca_selected_features[name] = [X_subset.columns[i] for i in top_indices]

Seleziona features trovate con PCA

In [11]:
for name in sequence_combinations:
    print(f"\n🔹 Features selected for {name}:")
    feats = pca_selected_features.get(name, [])
    if feats:
        for feat in feats:
            print(f"  - {feat}")
    else:
        print("  (nessuna feature selezionata)")
    print("-" * 80)


🔹 Features selected for ADC:
  - adc_original_shape_Flatness
  - adc_original_shape_Elongation
  - adc_wavelet-HLH_firstorder_RootMeanSquared
  - adc_wavelet-HLH_firstorder_Mean
  - adc_wavelet-LHH_firstorder_Median
  - adc_original_shape_Sphericity
  - adc_wavelet-HHH_firstorder_Mean
  - adc_wavelet-LHL_ngtdm_Contrast
  - adc_wavelet-HHL_firstorder_Mean
  - adc_wavelet-HHH_firstorder_RootMeanSquared
  - adc_original_glszm_LargeAreaLowGrayLevelEmphasis
  - adc_wavelet-LHH_firstorder_Mean
  - adc_wavelet-LHH_firstorder_Skewness
  - adc_wavelet-HHL_firstorder_RootMeanSquared
  - adc_wavelet-LHH_firstorder_RootMeanSquared
  - adc_wavelet-LLH_glcm_ClusterShade
  - adc_wavelet-HLH_firstorder_Median
  - adc_wavelet-HHL_firstorder_Skewness
  - adc_wavelet-HHH_glszm_LargeAreaLowGrayLevelEmphasis
  - adc_wavelet-HLL_gldm_LargeDependenceLowGrayLevelEmphasis
  - adc_wavelet-HHL_glcm_ClusterShade
  - adc_wavelet-HHH_ngtdm_Contrast
  - adc_wavelet-HHH_glcm_ClusterShade
  - adc_wavelet-HHH_glszm_La

In [23]:
print(len(feats))

50
